In [1]:
import h3
import pandas as pd
import geopandas as gpd
from shapely import geometry

import seaborn as sns

import numpy as np

from scipy import stats

import arviz as az
import pymc as pm
import patsy

from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline

from sklearn.dummy import DummyRegressor
from sklearn.linear_model import PoissonRegressor
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor

from sklearn.metrics import mean_squared_error
from sklearn.model_selection import train_test_split, GroupKFold, GroupShuffleSplit, RandomizedSearchCV

from sklearn.preprocessing import StandardScaler, OneHotEncoder

# 0. Data Read & Cleanup
Here we'll read in the data, drop a bunch of unnecessary columns, and also rename some columns to have cleaner names.

## Read data

In [2]:
gcs_path = 'gs://smart4'

count_data = pd.read_csv(f'{gcs_path}/count_file/modeling_data_mar30.csv')

unwanted_columns = [
    'Unnamed: 0',
    'X', 'ID',
    'ATT.in.Million',
    'bgarea_t', 'bgcliparea_t', 'pctofbgarea_t',
    'bgarea_q', 'bgcliparea_q', 'pctofbgarea_q',
    'bgarea_h', 'bgcliparea_h', 'pctofbgarea_h',
    'rt_i_shd_tot_width', 'lt_i_shd_tot_width',
    'near_strava_id', 
    'ATT.in.Thousands',
    'rowIndex', 'primary', 'secondary', 'tertiary', 'residential', 'trunk', 'secondary_link', 'unclassified',
    'speed_0_25', 'speed_21_35', 'speed_greater_than_35',
    'path', 'bike_lane',
    'bike_route', 'cycle_track', 'trail', 'Interstate', 'Freeway', 'Principal_Arterial',
    'Minor_Arterial', 'Major_Collector', 'Minor_Collector', 'Local'
]
count_data = count_data.drop(columns=unwanted_columns)

count_data['centroid'] = count_data.apply(lambda x: geometry.Point(x['Long'], x['Lat']), axis=1)
count_data = gpd.GeoDataFrame(count_data, geometry='centroid', crs=4326)

/opt/conda/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3553: DtypeWarning: Columns (7) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)
/opt/conda/lib/python3.7/site-packages/pandas/core/dtypes/cast.py:118: ShapelyDeprecationWarning: The array interface is deprecated and will no longer work in Shapely 2.0. Convert the '.coords' to a numpy array instead.
  arr = construct_1d_object_array_from_listlike(values)


In [3]:
count_data['log_AADB'] = count_data['AADB'].apply(np.log)

In [4]:
count_data.query('AADB != 0')[['centroid', 'log_AADB', 'AADB']].explore('log_AADB')

## Data cleanup

In [5]:
count_data = count_data.rename(columns={
    'Stv_commute_adb': 'strava_commute_adb',
    'Stv_leisure_adb': 'strava_leisure_adb',
    'Stv_Ave_speed': 'strava_average_speed'})

count_data['total_lanes'] = count_data['rt_lanes_amt'] + count_data['lt_lanes_amt']
count_data['strava_leisure_pct'] = \
    count_data['strava_leisure_adb']/(count_data[['strava_leisure_adb', 'strava_commute_adb']].sum(axis=1))

# These Class V and Class VI values seem to be garbage
count_data['bike_facs'] = count_data['bike_facs'].replace(
    {'Not Collected': 'Unknown', 
     # 'Class V': 'Unknown',
     'Class VI': 'Unknown',
     '0': 'Unknown'
    })

In [6]:
count_data['bike_facs'] = count_data['bike_facs'].str.strip().fillna('Unknown')
count_data['fclass'] = count_data['fclass'].fillna('unknown')

In [7]:
county_summaries = count_data.groupby('county')['AADB'].agg(['mean', 'std']).rename(columns=lambda col: f'county_AADB_{col}')
# very large if we don't know better
county_summaries['county_AADB_std'] = county_summaries['county_AADB_std'].fillna(500)
count_data = count_data.join(county_summaries, on='county')

In [8]:
count_data['outlier'] = (count_data['AADB'] > (count_data['county_AADB_mean'] + 5 * count_data['county_AADB_std']))

In [9]:
m = count_data.query('not outlier')[['tdg_id', 'year', 'AADB', 'outlier', 'centroid']].explore(color='blue')
m = count_data.query('outlier')[['tdg_id', 'year', 'AADB', 'outlier', 'centroid']].explore(color='red', m=m)
m

cool, let's go with 5 SD above the mean as our outlier threshold.

In [10]:
# Make some h3 Index values for stratification
count_data['h3_7'] = count_data.apply(lambda x: h3.geo_to_h3(x['Lat'], x['Long'], 7), axis=1)
count_data['h3_8'] = count_data.apply(lambda x: h3.geo_to_h3(x['Lat'], x['Long'], 8), axis=1)


## Make matrices

In [11]:
count_data.columns

Index(['Unnamed: 0.1', 'X.3', 'X.2', 'X.1', 'location', 'Lat', 'Long', 'year',
       'ATT', 'no_of_months_data_collected', 'type', 'AADB', 'matched_seg_id',
       'segment_id', 'street_name', 'county', 'tdg_id', 'lrs_cal_id',
       'bikes_proh', 'int_tdg_id', 'loc_id', 'seg_counter', 'fclass',
       'tasas_ids', 'ataip_ids', 'fc_draft', 'speed', 'slope',
       'empnum_density_t', 'pctwhite_t', 'totwhitepersqmi_t',
       'pctbiketowork_t', 'totbiketoworkpersqmi_t', 'pctatleastbachelors_t',
       'totatleastbachelorspersqmi_t', 'pctnoveh_t', 'totnovehpersqmi_t',
       'popdensitysqmi_t', 'hshlddensitysqmi_t', 'pctwhite_q',
       'totwhitepersqmi_q', 'pctbiketowork_q', 'totbiketoworkpersqmi_q',
       'pctatleastbachelors_q', 'totatleastbachelorspersqmi_q', 'pctnoveh_q',
       'totnovehpersqmi_q', 'popdensitysqmi_q', 'hshlddensitysqmi_q',
       'pctwhite_h', 'totwhitepersqmi_h', 'pctbiketowork_h',
       'totbiketoworkpersqmi_h', 'pctatleastbachelors_h',
       'totatleastbache

In [12]:
demographic_col_templates = [
    'popdensitysqmi_{}', 'hshlddensitysqmi_{}',
    'empnum_density_{}', 'pctwhite_{}', 'pctbiketowork_{}', 'pctatleastbachelors_{}', 
    'pctnoveh_{}']

demographic_cols = []
for distance in ('t', 'q', 'h'):
    demographic_cols += [col.format(distance) for col in demographic_col_templates]
    
strava_cols = ['strava_commute_adb', 'strava_leisure_adb', 'strava_average_speed', 'strava_leisure_pct']

data_mask = ~count_data.outlier

count_data_clean = count_data[data_mask].reset_index(drop=True)

y_col = 'AADB'
x_cols = ['bike_facs', 
          # 'fclass',  - just use the official one
          'fc_draft', 'speed', 'slope', 
          # 'adt_amt', 'total_lanes', ## - these were included, but are almost entirely Null
          'near_univ_miles', 'near_large_univ_miles'] + strava_cols + demographic_cols 


X = count_data_clean[x_cols]
y = count_data_clean[y_col]


ADT and number of lanes are almost entirely missing data.

Everything else likely makes sense to fill with 0s.

In [13]:
X = X.fillna(0)

# 1. Set up train-test splits
Here we're going to use a grouped train/test split, grouped based on the `h3` index at resolution 7. This is to try to prevent information leakage from locations that are spatially adjacent. It's not perfect, but it should help (other than in edge cases of counts right on either side of a grid cell line).

In [14]:
TEST_SIZE = 0.2
GROUPER_COL = 'h3_7'


In [15]:
grouper = count_data_clean[GROUPER_COL]

In [16]:
train_indx, test_indx = next(GroupShuffleSplit(random_state=42,test_size=TEST_SIZE).split(X, y, grouper))

X_train, X_test, y_train, y_test = X.loc[train_indx, :], X.loc[test_indx, :], y[train_indx], y[test_indx]

grouper_train = count_data[GROUPER_COL][train_indx]

In [17]:
print(f"Test set is {len(test_indx)/(len(test_indx) + len(train_indx)) * 100 :.2f}% of sample")

Test set is 19.82% of sample


# 2. Model Fitting
Now we'll start estimating models. First let's set up a container for storing results.


In [18]:
model_results = {}

def evaluate_model(model, X_train=X_train, y_train=y_train, X_test=X_test, y_test=y_test):
    
    results = {
        'in_sample_rmse': mean_squared_error(y_train, model.predict(X_train), squared=False),
        'out_sample_rmse': mean_squared_error(y_test, model.predict(X_test), squared=False),
        'model': model
    }
    print(results)
    return results


def model_cv(model, cv_params, n_iter=25):
    """Convenience function for doing cross-validation and evaluating the best model"""
    
    cv = RandomizedSearchCV(
        estimator=model,
        param_distributions=cv_params,
        cv=gkf.split(X_train, y_train, grouper_train),
        n_iter=n_iter,
        verbose=1
    )
    
    cv.fit(X_train, y_train)
    
    best_model = cv.best_estimator_
    
    return evaluate_model(best_model)

Make a set of folds for doing cross-validation for hyperparam tuning

In [19]:
gkf = GroupKFold()

## 2a. Dummy Model
As usual, the first thing we'll do is set a baseline for model accuracy by estimating a no-skill model.

In [20]:
dummy_model = DummyRegressor()
dummy_model.fit(X_train, y_train)

model_results['dummy'] = evaluate_model(dummy_model)

{'in_sample_rmse': 287.1765570533578, 'out_sample_rmse': 171.9332656673369, 'model': DummyRegressor()}


## 2b. Vanilla Poisson Regression
Here we'll one-hot encode categoricals, standard scale everything else, and dump into a Poisson regression. We'll also tune the regularization on the Poisson.

In [21]:
categorical_cols = ['bike_facs', 'fc_draft']
categorical_drop_vals = ['Unknown', 7]

numeric_cols = [col for col in X_train.columns if col not in categorical_cols]

base_column_transformers = [
    ('categoricals', OneHotEncoder(drop=categorical_drop_vals), categorical_cols),
    ('standard_scale', StandardScaler(), numeric_cols)
]

In [22]:
vanilla_poisson_model = Pipeline(
    [
        ('transform', ColumnTransformer(base_column_transformers,)),
        ('poisson', PoissonRegressor(max_iter=1000))
    ])

vanilla_poisson_params = {'poisson__alpha': stats.uniform(0, 3),}

In [23]:
model_results['vanilla_poisson'] = model_cv(vanilla_poisson_model, vanilla_poisson_params)

Fitting 5 folds for each of 25 candidates, totalling 125 fits
{'in_sample_rmse': 183.97673938260536, 'out_sample_rmse': 148.39549280869446, 'model': Pipeline(steps=[('transform',
                 ColumnTransformer(transformers=[('categoricals',
                                                  OneHotEncoder(drop=['Unknown',
                                                                      7]),
                                                  ['bike_facs', 'fc_draft']),
                                                 ('standard_scale',
                                                  StandardScaler(),
                                                  ['speed', 'slope',
                                                   'near_univ_miles',
                                                   'near_large_univ_miles',
                                                   'strava_commute_adb',
                                                   'strava_leisure_adb',
                        

In [24]:
p = model_results['vanilla_poisson']['model'].named_steps['poisson']

In [25]:
pd.Series(
    data=p.coef_, 
    index=model_results['vanilla_poisson']['model'][:-1].get_feature_names_out())

categoricals__bike_facs_Class I          0.487316
categoricals__bike_facs_Class II         0.023035
categoricals__bike_facs_Class III        0.022684
categoricals__bike_facs_Class IV        -0.214737
categoricals__bike_facs_Class V          0.088111
categoricals__fc_draft_1                 0.017130
categoricals__fc_draft_2                 0.123270
categoricals__fc_draft_3                 0.006134
categoricals__fc_draft_4                 0.065055
categoricals__fc_draft_5                 0.072542
categoricals__fc_draft_6                -0.013553
standard_scale__speed                    0.077020
standard_scale__slope                   -0.104146
standard_scale__near_univ_miles         -0.132366
standard_scale__near_large_univ_miles   -0.048396
standard_scale__strava_commute_adb       0.097950
standard_scale__strava_leisure_adb       0.114239
standard_scale__strava_average_speed    -0.001183
standard_scale__strava_leisure_pct      -0.022809
standard_scale__popdensitysqmi_t        -0.256424


Yikes, the out-of-sample RMSE is horrible! Let's try a tree-based model, then we'll try some interactions.

## 2c. Random Forest Regression

In [35]:
rfr_model = Pipeline(
    [
        ('transform', ColumnTransformer(base_column_transformers,)),
        ('rfr', RandomForestRegressor())
    ])

rfr_params = {
        'rfr__n_estimators': [10, 25, 100],
        'rfr__min_samples_split': [2, 3, 4, 5],
        'rfr__min_samples_leaf': [2, 5, 10],
        'rfr__max_features': ['sqrt', 1.],
        'rfr__max_depth': [10, 25, 100, 500, 1000],
    }

model_results['rfr'] = model_cv(rfr_model, rfr_params, 50)

Fitting 5 folds for each of 50 candidates, totalling 250 fits
{'in_sample_rmse': 101.6363138072033, 'out_sample_rmse': 154.07833360462072, 'model': Pipeline(steps=[('transform',
                 ColumnTransformer(transformers=[('categoricals',
                                                  OneHotEncoder(drop=['Unknown',
                                                                      7]),
                                                  ['bike_facs', 'fc_draft']),
                                                 ('standard_scale',
                                                  StandardScaler(),
                                                  ['speed', 'slope',
                                                   'near_univ_miles',
                                                   'near_large_univ_miles',
                                                   'strava_commute_adb',
                                                   'strava_leisure_adb',
                         

## 2d. Gradient Boosting Regressor

In [36]:
gbr_model = Pipeline(
    [
        ('transform', ColumnTransformer(base_column_transformers,)),
        ('gbr', GradientBoostingRegressor(random_state=42))
    ])

gbr_params = {
    'gbr__learning_rate': stats.expon(1, 10),
    'gbr__n_estimators': [10, 100, 250, 500, 1000],
    'gbr__min_samples_split': stats.uniform(),
    'gbr__max_depth': stats.randint(1, 10),
#    'gbr__min_impurity_decrease': stats.expon(1, 10),
}

model_results['gbr'] = model_cv(gbr_model, gbr_params, 10)

Fitting 5 folds for each of 10 candidates, totalling 50 fits


/opt/conda/lib/python3.7/site-packages/numpy/core/fromnumeric.py:86: RuntimeWarning: overflow encountered in reduce
  return ufunc.reduce(obj, axis, dtype, out, **passkwargs)
/opt/conda/lib/python3.7/site-packages/numpy/core/fromnumeric.py:86: RuntimeWarning: overflow encountered in reduce
  return ufunc.reduce(obj, axis, dtype, out, **passkwargs)
/opt/conda/lib/python3.7/site-packages/numpy/core/fromnumeric.py:86: RuntimeWarning: overflow encountered in reduce
  return ufunc.reduce(obj, axis, dtype, out, **passkwargs)
/opt/conda/lib/python3.7/site-packages/sklearn/ensemble/_gb_losses.py:231: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/opt/conda/lib/python3.7/site-packages/sklearn/ensemble/_gb_losses.py:231: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/opt/conda/lib/python3.7/site-packages/sklearn/ensemble/_gb_losses.py:231: RuntimeWarning: overflow e

KeyboardInterrupt: 

In [38]:
X_train.columns

Index(['bike_facs', 'fc_draft', 'speed', 'slope', 'near_univ_miles',
       'near_large_univ_miles', 'strava_commute_adb', 'strava_leisure_adb',
       'strava_average_speed', 'strava_leisure_pct', 'popdensitysqmi_t',
       'hshlddensitysqmi_t', 'empnum_density_t', 'pctwhite_t',
       'pctbiketowork_t', 'pctatleastbachelors_t', 'pctnoveh_t',
       'popdensitysqmi_q', 'hshlddensitysqmi_q', 'empnum_density_q',
       'pctwhite_q', 'pctbiketowork_q', 'pctatleastbachelors_q', 'pctnoveh_q',
       'popdensitysqmi_h', 'hshlddensitysqmi_h', 'empnum_density_h',
       'pctwhite_h', 'pctbiketowork_h', 'pctatleastbachelors_h', 'pctnoveh_h'],
      dtype='object')

## 2e. Poisson Mixture Model

In [19]:
y_new, X_new = patsy.dmatrices('AADB ~ strava_leisure_adb + strava_commute_adb', data=count_data_clean, return_type='dataframe')

X_train_new, X_test_new, y_train_new, y_test_new = X_new.loc[train_indx, :], X_new.loc[test_indx, :], y_new.loc[train_indx], y_new.loc[test_indx]

In [20]:
X_train_new

Intercept  strava_leisure_adb  strava_commute_adb
0           1.0           12.328767            0.705479
1           1.0           12.328767            0.705479
2           1.0           12.684932            0.712329
3           1.0           11.972603            0.698630
4           1.0            0.712329            0.431507
...         ...                 ...                 ...
4217        1.0            0.219178            0.013699
4218        1.0           17.205479            0.328767
4220        1.0           19.328767            0.383562
4221        1.0           17.452055            0.397260
4222        1.0           19.315068            0.726027

[3386 rows x 3 columns]

In [21]:
coords = {'coeffs': X_new.columns}

with pm.Model(coords=coords) as model:
    # Define data
    X = pm.MutableData('X', X_train_new.values)
    y = pm.MutableData('y', y_train_new.values)
    
    # Define priors
    #sigma = pm.HalfCauchy("sigma", beta=10)
    alpha = pm.Normal("Intercept", 0, sigma=20)
    b_strava_leisure = pm.Normal("strava_leisure_adb", 0, sigma=20)
    b_strava_commute = pm.Normal("strava_commmute_adb", 0, sigma=20)

    lambda_ = alpha + b_strava_leisure * X[:, 1] + b_strava_commute * X[:, 2]
    
    # Define likelihood
    likelihood = pm.Poisson("obs", mu=pm.math.exp(lambda_), observed=y)

    # Inference!
    # draw 500 posterior samples using NUTS sampling
    idata = pm.sample(10)

Only 10 samples in chain.
Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (2 chains in 2 jobs)
NUTS: [Intercept, strava_leisure_adb, strava_commmute_adb]


ValueError: Not enough samples to build a trace.

In [ ]:
az.plot_trace(idata)

In [ ]:
with model:
    pm.set_data(

In [ ]:
pm.sample_posterior_predictive(

## 2. Comparison of models

In [ ]:
display(pd.DataFrame(model_results).T)